# Feature Engineering

## 01 Missing Values

Dataset source: https://www.kaggle.com/kevinmh/fifa-18-more-complete-player-dataset

In [2]:
import pandas as pd
import numpy as np
df = pd.read_csv('fifa18_complete.csv', encoding='utf_8')

In [3]:
pd.set_option('display.max_rows',100)

In [4]:
def nas_sorted(df):
    return df.isnull().sum().sort_values(ascending = False)

In [5]:
pd.set_option('display.max_columns', 500)

In [6]:
df.T

0      \
ID                                                                        20801   
name                                                          Cristiano Ronaldo   
full_name                                          C. Ronaldo dos Santos Aveiro   
club                                                             Real Madrid CF   
club_logo                               https://cdn.sofifa.org/18/teams/243.png   
special                                                                    2228   
age                                                                          32   
league                                                 Spanish Primera División   
birth_date                                                           1985-02-05   
height_cm                                                                   185   
weight_kg                                                                    80   
body_type                                                            C. Ronaldo   
real_face                                                                  True   
flag                                     https://cdn.sofifa.org/flags/38@3x.png   
nationality                                                            Portugal   
photo                               https://cdn.sofifa.org/18/players/20801.png   
eur_value                                                              9.55e+07   
eur_wage                                                                 565000   
eur_release_clause                                                    1.958e+08   
overall                                                                      94   
potential                                                                    94   
pac                                                                          90   
sho                                                                          93   
pas                                                                          82   
dri                                                                          90   
def                                                                          33   
phy                                                                          80   
international_reputation                                                      5   
skill_moves                                                                   5   
weak_foot                                                                     4   
work_rate_att                                                              High   
work_rate_def                                                               Low   
preferred_foot                                                            Right   
crossing                                                                     85   
finishing                                                                    94   
heading_accuracy                                                             88   
short_passing                                                                83   
volleys                                                                      88   
dribbling                                                                    91   
curve                                                                        81   
free_kick_accuracy                                                           76   
long_passing                                                                 77   
ball_control                                                                 93   
acceleration                                                                 89   
sprint_speed                                                                 91   
agility                                                                      89   
reactions                                                                    96   
balance                                                                      63   
shot_po

In [7]:
sorted_nas = nas_sorted(df)

In [8]:
sorted_nas[:32]

gk                    15973
lcb                    2021
lw                     2021
rw                     2021
rf                     2021
ram                    2021
rcm                    2021
rm                     2021
rdm                    2021
rcb                    2021
rb                     2021
rwb                    2021
st                     2021
cf                     2021
ldm                    2021
cam                    2021
cm                     2021
lm                     2021
cdm                    2021
cb                     2021
lb                     2021
lwb                    2021
ls                     2021
lf                     2021
lam                    2021
rs                     2021
lcm                    2021
eur_release_clause     1494
club                    253
club_logo               253
league                  253
dri                       0
dtype: int64

### Find outliers 

Sometimes our missing value numbers are not stored as numbers that we cannot predict. We may discover them to be outliers in our dataset. It's a good idea to have some methods so that we can explore outliers in our dataset.

In [9]:
df.columns = df.columns.str.lstrip()

In [10]:
np.arange(-3, 4, 1)

array([-3, -2, -1,  0,  1,  2,  3])

In [11]:
from scipy import stats

def percentiles(column):
    z_scores = stats.zscore(column)
    # segment based on number of standard deviations away from the mean     
    hist, bin_edges = np.histogram(z_scores, bins=np.arange(-3, 4, 1), density=True)
    return np.stack((hist, bin_edges[1:]))

In [12]:
percentiles(df['eur_value'])

array([[ 0.        ,  0.        ,  0.78261116,  0.15855866,  0.04559339,
         0.01323679],
       [-2.        , -1.        ,  0.        ,  1.        ,  2.        ,
         3.        ]])

In [13]:
def too_many_outliers(column, threshold = .05):
    #  expected .021 if normal distribution
    z_less_neg_two = percentiles(column)[0, 0]
    z_gt_two = percentiles(column)[0, -1]
    if z_less_neg_two > threshold or z_gt_two > threshold:
        return np.hstack((column.name, z_less_neg_two, z_gt_two))
    else:
        False

In [14]:
def outlier_columns(df, threshold = .05):
    numeric_columns = df.select_dtypes(include=['float64', 'int64']).columns
    outlier_columns = np.array([too_many_outliers(df[column]) for column in numeric_columns])
    return np.array([column for column in outlier_columns if column is not None])

In [15]:
def select_outliers(column, upper_tail = True):
    if upper_tail:
        return column[stats.zscore(column) > 2]
    else:
        return column[stats.zscore(column) < -2]

In [18]:
np.seterr(divide='ignore', invalid='ignore') # to solve RuntimeWarning: invalid value encountered in divide

outlier_columns(df)

array([['special', '0.05066459040097881', '0.0045047550191869195'],
       ['international_reputation', '0.0', '0.08008621178605865'],
       ['skill_moves', '0.0', '0.05090787568229921'],
       ['heading_accuracy', '0.08925197287984885',
        '0.0015560742469712125'],
       ['short_passing', '0.07020280811232449', '0.0008357477156229106'],
       ['dribbling', '0.09075247304657108', '0.00011114816049794375'],
       ['ball_control', '0.09508725130599088', '0.000444592641991775'],
       ['stamina', '0.06169336893635959', '0.0'],
       ['composure', '0.05290149952617203', '0.006354869279224037'],
       ['gk_diving', '0.0', '0.0752861333179962'],
       ['gk_handling', '0.0', '0.07795930065921468'],
       ['gk_kicking', '0.0', '0.08015550854725287'],
       ['gk_positioning', '0.0', '0.07055302986706566'],
       ['gk_reflexes', '0.0', '0.07493525179856116']], dtype='<U32')

In [17]:
select_outliers(df['eur_value']).value_counts()

14000000.0     36
13500000.0     35
14500000.0     27
17500000.0     24
18000000.0     23
15000000.0     21
17000000.0     20
16000000.0     16
15500000.0     16
16500000.0     16
21000000.0     14
23000000.0     13
24500000.0     13
20500000.0     12
20000000.0     12
25000000.0     11
18500000.0     11
21500000.0     10
30500000.0     10
19500000.0     10
26000000.0      9
22000000.0      9
24000000.0      8
22500000.0      7
19000000.0      7
25500000.0      7
28000000.0      6
27500000.0      6
23500000.0      5
31500000.0      5
29000000.0      5
34000000.0      5
27000000.0      5
29500000.0      5
31000000.0      4
26500000.0      4
33000000.0      4
37500000.0      4
48500000.0      4
28500000.0      4
35500000.0      3
38000000.0      3
30000000.0      3
36000000.0      3
59000000.0      3
44000000.0      3
32500000.0      3
46000000.0      3
32000000.0      3
42000000.0      2
66500000.0      2
43000000.0      2
39000000.0      2
40000000.0      2
44500000.0      2
64500000.0

### Add Columns

In [89]:
def informative(df):
    non_informative = [column for column in df.columns if len(df[column].unique()) == 1]
    informative_columns = list(set(df.columns.to_list()) - set(non_informative))
    return df[informative_columns]
    
def some_nans(df):
    informative_df = informative(df)
    some_nans_bools = pd.isnull(informative_df).any()
    return some_nans_bools.index[some_nans_bools]
    
def new_na_columns(df):
    nan_columns = some_nans(df)
    df_nans = pd.isnull(df[nan_columns])
    column_name_nas = ["{column_nan}_is_na".format(column_nan = column_nan) for column_nan in nan_columns]
    df_nans.columns = column_name_nas
    return df_nans

def new_df_with_na_cols(df):
    return pd.concat([df, new_na_columns(df)], axis = 1)

In [90]:
len(df.columns)

185

In [91]:
len(informative(df).columns)

159

In [92]:
df_with_na_cols = new_df_with_na_cols(df)

In [93]:
len(df_with_na_cols.columns)

216

### Impute Means

In [94]:
# def impute_means_on_nas(df):
#     copied_df = df.copy()
#     mean_series = df.mean(axis = 0, skipna = True, numeric_only = True)
#     values = dict(zip(mean_series.index, mean_series.values))
#     copied_df.fillna(value = values)
#     return copied_df

## 02 DateTimes

Deciding which features should be included and focused on in our linear model is an important skill of any data scientist. As we saw previously, if we include features which are too collinear, we will improperly measure the coefficients related to our collinear features. In addition, feature selection and prioritizing features with feature importance will help us to understand which features to devote our attention to in terms of feature engineering and domain understanding. Finally, limiting the number of features in our model, and identifying the most crucial features in our model will make our models, and their insights more understandable.

In [95]:
df.shape

(17994, 185)

As we can see, our dataset as 17994 rows and close to 185 features. Our goal is to predict the overall.

In [96]:
df.columns

Index(['ID', 'name', 'full_name', 'club', 'club_logo', 'special', 'age',
       'league', 'birth_date', 'height_cm',
       ...
       'prefers_cb', 'prefers_lb', 'prefers_lwb', 'prefers_ls', 'prefers_lf',
       'prefers_lam', 'prefers_lcm', 'prefers_ldm', 'prefers_lcb',
       'prefers_gk'],
      dtype='object', length=185)

Some of these columns include data that we do not know how to handle - mainly textual data and images. A lot of this data is simply not in the correct format. Let's take a look.

Let's try to capture as much of this object data as possible. In this lesson, we'll start with date values.

In [97]:
df.dtypes

ID                                      int64
name                                   object
full_name                              object
club                                   object
club_logo                              object
special                                 int64
age                                     int64
league                                 object
birth_date                             object
height_cm                             float64
weight_kg                             float64
body_type                              object
real_face                                bool
flag                                   object
nationality                            object
photo                                  object
eur_value                             float64
eur_wage                              float64
eur_release_clause                    float64
overall                                 int64
potential                               int64
pac                               

In [98]:
def find_object_features(df):
    return list(df.dtypes[df.dtypes == 'object'].index)

In [99]:
len(find_object_features(df))

13

In [100]:
def contains_date(column):
    regex_string = (r'^\d{1,2}-\d{1,2}-\d{4}$|^\d{4}-\d{1,2}-\d{1,2}$' + 
'|^\d{1,2}\/\d{1,2}\/\d{4}$|^\d{4}\/\d{1,2}\/\d{1,2}$')
    return column.str.contains(regex_string).any()

The regex above is wild but it's easier to understand once we understand that each `|` means `or`.  So really, we can think of the above regex as multiple different ones.  So the first one of them is:

`^\d{1,2}-\d{1,2}-\d{4}$`

Which means start with one or two digits, then one or two digits again, and then four digits.  With each set of digits separated by a hyphen.

`11-22-2018`

So contains date tells us if any column in the above contains a date.

In [101]:
def find_date_features(df):
    series_contains_date = df.apply(contains_date)
    return series_contains_date.index[series_contains_date.values]

In [102]:
date_features = find_date_features(df)

In [103]:
date_features

Index(['birth_date'], dtype='object')

Now we can set those features to be date time.

In [104]:
def to_dates(df):
    date_features = find_date_features(df)
    return df[date_features].astype('datetime64[ns]')

In [105]:
df_date_features = to_dates(df)

In [106]:
df_date_features.dtypes
df_date_features[:1]

birth_date
0 1985-02-05

In [107]:
from date_lib import add_datepart

In [108]:
def generate_new_date_columns(dates_df):
    copied_dates_df = dates_df.copy()
    for col in copied_dates_df.columns:
        add_datepart(copied_dates_df, col)
    return copied_dates_df

In [109]:
new_date_col_df = generate_new_date_columns(df_date_features)

In [110]:
len(new_date_col_df.columns)

13

Once coercing our dates, we can merge with the original dataframe, and replace each of the old columns that should be dates.

In [111]:
def merge_dfs(original_df, new_df):
    copied_original = original_df.copy()
    date_features = find_date_features(original_df)
    copied_dropped = copied_original.drop(columns = date_features)
    copied_dropped[new_df.columns] = new_df
    return copied_dropped

In [112]:
new_df = merge_dfs(df, new_date_col_df)

We can confirm that the `new_df` has fewer `object_feature` columns than the original.

In [113]:
# new_df = new_df.drop(columns = remaining_date_features)
len(find_object_features(new_df))

12

In [114]:
len(find_object_features(df))

13

Even though our `new_df` has more features.

In [115]:
len(new_df.columns)

197

# 03 Numerical Data

In [116]:
def find_object_features(df):
    return list(df.dtypes[df.dtypes == 'object'].index)

In [117]:
len(find_object_features(df))

13

In [118]:
def find_object_feature_values(df):
    object_features = find_object_features(df)
    return df[object_features][:2].values

In [119]:
def contains_numbers(column):
    # matches price or percentage     
    regex_string = (r'^(?!.*www|.*-|.*\/|.*[A-Za-z]|.* ).*\d.*')
#     regex_string = (r'\$\d+.*|\d+.*\%$|^\d+.*$')
    return column.str.contains(regex_string).all()

In [120]:
contains_numbers(df.birth_date)

False

In [121]:
def find_numeric_features(df):
    series_contains_number = df.apply(contains_numbers)
    return series_contains_number.index[series_contains_number.values]

In [122]:
numeric_features = find_numeric_features(df)

In [123]:
numeric_features

Index(['ID', 'special', 'age', 'height_cm', 'weight_kg', 'real_face',
       'eur_value', 'eur_wage', 'eur_release_clause', 'overall',
       ...
       'prefers_cb', 'prefers_lb', 'prefers_lwb', 'prefers_ls', 'prefers_lf',
       'prefers_lam', 'prefers_lcm', 'prefers_ldm', 'prefers_lcb',
       'prefers_gk'],
      dtype='object', length=172)

While the `find_numeric_features` method captures the numeric features, we want to narrow down the features that we should fix.

In [124]:
def numeric_to_fix(df):
    numeric_features = find_numeric_features(df)
    return df[numeric_features].select_dtypes(exclude=['int64', 'float64'])[0:2]

In [125]:
numeric_to_fix(df)

real_face  1_on_1_rush_trait  acrobatic_clearance_trait  \
0       True              False                      False   
1       True              False                      False   

   argues_with_officials_trait  avoids_using_weaker_foot_trait  \
0                        False                           False   
1                        False                           False   

   backs_into_player_trait  bicycle_kicks_trait  cautious_with_crosses_trait  \
0                    False                False                        False   
1                    False                False                        False   

   chip_shot_trait  chipped_penalty_trait  comes_for_crosses_trait  \
0            False                  False                    False   
1             True                  False                    False   

   corner_specialist_trait  diver_trait  dives_into_tackles_trait  \
0                    False        False                     False   
1                    False        False                     False   

   diving_header_trait  driven_pass_trait  early_crosser_trait  \
0                False              False                False   
1                False              False                False   

   fan's_favourite_trait  fancy_flicks_trait  finesse_shot_trait  flair_trait  \
0                  False               False               False         True   
1                  False               False                True        False   

   flair_passes_trait  gk_flat_kick_trait  gk_long_throw_trait  \
0               False               False                False   
1               False               False                False   

   gk_up_for_corners_trait  giant_throw_in_trait  inflexible_trait  \
0                    False                 False             False   
1                    False                 False             False   

   injury_free_trait  injury_prone_trait  leadership_trait  long_passer_trait  \
0              False               False             False              False   
1              False               False             False              False   

   long_shot_taker_trait  long_throw_in_trait  one_club_player_trait  \
0                   True                False                  False   
1                   True                False                   True   

   outside_foot_shot_trait  playmaker_trait  power_free_kick_trait  \
0                    False            False                   True   
1                    False             True                  False   

   power_header_trait  puncher_trait  rushes_out_of_goal_trait  \
0               False          False                     False   
1               False          False                     False   

   saves_with_feet_trait  second_wind_trait  selfish_trait  \
0                  False              False          False   
1                  False              False          False   

   skilled_dribbling_trait  stutter_penalty_trait  swerve_pass_trait  \
0                     True                  False              False   
1                     True                  False              False   

   takes_finesse_free_kicks_trait  target_forward_trait  team_player_trait  \
0                           False                 False              False   
1                           False                 False              False   

   technical_dribbler_trait  tries_to_beat_defensive_line_trait  \
0                     False                               False   
1                     False                               False   

   poacher_speciality  speedster_speciality  aerial_threat_speciality  \
0               False                  True                     False   
1               False                 False                     False   

   dribbler_speciality  playmaker_speciality  engine_speciality  \
0                 True                 False              False   
1                 True                

### Modifying Values

Since these values are booleans values, we are going to a bbooleans value cleaning

# 04 Boolean Values

In [126]:
def find_object_features(df):
    return list(df.dtypes[df.dtypes == 'object'].index)

In [127]:
def find_object_feature_values(df):
    object_features = find_object_features(df)
    return df[object_features][:1].values[0]

In [128]:
import numpy as np
def find_booleans(df):
    columns = df.columns
    boolean_columns = np.array([column for column in columns if len(df[column].value_counts(dropna=True)) == 2])
    boolean_values = np.array([df[column].value_counts(dropna=True).index.to_list() for column in boolean_columns])
    columns_and_values = np.stack((boolean_columns, boolean_values[:, 0], boolean_values[:, 1])).T
    return columns_and_values

In [129]:
boolean_columns = find_booleans(df)

In [130]:
def select_booleans(df, values = []):
    boolean_columns = find_booleans(df)
    matches = np.isin(boolean_columns[:, 1], values)
    return boolean_columns[matches]

In [146]:
boolean_values = ['True', 'False']
matrix_potential_booleans = select_booleans(df, boolean_values)

boolean_df = df[matrix_potential_booleans[:, 0]]

In [138]:
boolean_mapping = {True: True, False: False}

In [139]:
def to_booleans(df, boolean_mapping):
    potential_columns = find_booleans(df)
    boolean_values = list(boolean_mapping.keys())
    boolean_features = select_booleans(df, boolean_values)[:, 0]
    boolean_df = pd.DataFrame({})
    for feature in boolean_features:
        boolean_df[feature] = df[feature].map(boolean_mapping)
    return boolean_df[boolean_features]

In [157]:
# new_boolean_cols = to_booleans(df, boolean_mapping)
boolean_df.iloc[0, 0] == 'True'


True

# 05 Categorical Features

In [19]:
def find_object_features(df):
    return list(df.dtypes[df.dtypes == 'object'].index)